In [1]:
import xarray as xr
from pathlib import Path
import glob


In [2]:
from dask_jobqueue import PBSCluster
cluster = PBSCluster()

In [3]:
cluster.scale(150) 

In [14]:
from dask.distributed import performance_report, Client
client = Client(cluster)

In [15]:
client

<Client: 'tcp://10.148.0.160:50358' processes=168 threads=168, memory=720.72 GB>

In [16]:
!qstat -u todaka -n


datarmor0: 
                                                            Req'd  Req'd   Elap
Job ID          Username Queue    Jobname    SessID NDS TSK Memory Time  S Time
--------------- -------- -------- ---------- ------ --- --- ------ ----- - -----
8740787.datarmo todaka   ice_mt   jupyterhub   5008   1   4   16gb 02:00 R 00:11
   r1i4n6/0*4
8740815.datarmo todaka   mpi_1    jupyter_wo  14824   1  28  120gb 24:00 R 00:05
   r2i0n20/0*28
8740817.datarmo todaka   mpi_1    jupyter_wo  14337   1  28  120gb 24:00 R 00:05
   r2i0n30/0*28
8740819.datarmo todaka   mpi_1    jupyter_wo   4607   1  28  120gb 24:00 R 00:05
   r2i0n32/0*28
8740820.datarmo todaka   mpi_1    jupyter_wo  24907   1  28  120gb 24:00 R 00:05
   r2i0n33/0*28
8740833.datarmo todaka   mpi_1    jupyter_wo  29791   1  28  120gb 24:00 R 00:04
   r2i0n21/0*28
8740834.datarmo todaka   mpi_1    jupyter_wo  32406   1  28  120gb 24:00 R 00:04
   r2i0n31/0*28


**Cleaning up tests before 
unmount tar file
This is done in a separate script 'unmount_tar.sh'



## Copy real netcdf Data from datalake

On datarmor compute node, i can't access internet/(can not access to synthetic data example) thus used real data available on datalake.
/home/ref-oc-public/modeles_marc/f1_e4000/best_estimate/2014/MARC_F1-MARS3D-MANGAE4000_201412312300Z.nc
These are hourly netcdf computed output.
here we use every day for one year, but just from 23:00
This is done in a separate script 'create_realdata.sh'


size of the tar file is:

In [17]:
!du -hs data/realdata.tar

6.1G	data/realdata.tar


## ratarmount

We will use [ratarmount](https://github.com/mxmlnkn/ratarmount) to create an index file with file names, ownership, permission flags, and offset information to be stored at the TAR file's location. Once the index is created, ratarmount then offers a FUSE mount integration for easy access to the files.

**NOTE:** Since `ratarmount` uses FUSE to mount the TAR file as a "filesystem in user space", you will need FUSE installed.  On OSX, you will need to install [osxfuse](https://osxfuse.github.io/) *by hand*.  On Linux, you can install `libfuse` using `conda`, if it is not already installed on your system.

**NOTE:** If you have `libfuse` on your system and it is *older* than October 19, 2018 (i.e., < 3.3.0 for `fuse3` or < 2.9.9 for `fuse2`), and you have either Lustre or GPFS filesystems, `ratarmount` will fail with an error saying that your filesystem is unsupported.  The solution is to upgrade to a newer version of `libfuse`.

**NOTE:** If you install the `libfuse` Conda-Forge package on a Linux system, then you need to set the `FUSE_LIBRARY_PATH` environment variable to the location of the `libfuse.so` library file (e.g., `export FUSE_LIBRARY_PATH=/path/to/libfuse3.so`).  If you do not do this, then `fusepy` (another dependency of `ratarmount`) will use the system `libfuse.so` file, which might be old.

**NOTE:** Currently, the Conda-Forge version of `libfuse` does *not* build the `libfuse` utilities such as `fusermount3`.  However, `fusepy` uses these utility functions under the hood when trying to mount the userspace filesystem.  If you install the most recent version of `libfuse` and properly set the location of `libfuse` so that `fusepy` can find it (i.e., `FUSE_LIBRARY_PATH`), you will get an error the `fusermount3` cannot be found.

mounting with ratarmount on each nodes are done in a separate script 'mount_tar.sh'


verify the number of netcdf files in each mounted point

In [19]:
!./verify_mount.sh

r1i4n6 NFS
365
r1i4n6 gpfs
365
r1i4n6 lustre
365
r2i0n20 NFS
365
r2i0n20 gpfs
365
r2i0n20 lustre
365
r2i0n30 NFS
365
r2i0n30 gpfs
365
r2i0n30 lustre
365
r2i0n32 NFS
365
r2i0n32 gpfs
365
r2i0n32 lustre
365
r2i0n33 NFS
ls: No match.
0
r2i0n33 gpfs
365
r2i0n33 lustre
365
r2i0n21 NFS
365
r2i0n21 gpfs
365
r2i0n21 lustre
365
r2i0n31 NFS
365
r2i0n31 gpfs
365
r2i0n31 lustre
365


For comparison, this is how long it takes to `list` the original data directory.

In [20]:
%%time
mounted_dir = Path("mounted_dataset/data/realdata/")
list(mounted_dir.iterdir())

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 4.24 ms


[PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140101T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140102T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140103T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140104T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140105T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140106T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140107T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140108T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140109T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140110T2300Z.nc'),
 PosixPath('mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140111T2300Z.nc'),
 PosixPath('mounted_d

In [21]:
%%time
mounted_dir = Path("data/realdata/")
list(mounted_dir.iterdir())

CPU times: user 8 ms, sys: 0 ns, total: 8 ms
Wall time: 84.1 ms


[PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140101T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140102T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140103T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140104T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140105T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140106T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140107T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140108T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140109T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140110T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140111T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140112T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000_20140113T2300Z.nc'),
 PosixPath('data/realdata/MARC_F1-MARS3D-MANGAE4000

**NFS=> tar 4.48 ms  real file 3.34 ms 

In [22]:
%%time
mounted_dir = Path("data_gpfs/mounted_dataset/data/realdata/")
list(mounted_dir.iterdir())

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 3.98 ms


[PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140101T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140102T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140103T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140104T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140105T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140106T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140107T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140108T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140109T2300Z.nc'),
 PosixPath('data_gpfs/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140110T2300Z.nc'),
 PosixPath

In [23]:
%%time
mounted_dir = Path("data_gpfs/realdata/")
list(mounted_dir.iterdir())

CPU times: user 0 ns, sys: 4 ms, total: 4 ms
Wall time: 2.14 ms


[PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140907T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20141019T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140727T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140123T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20141009T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140411T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140405T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140902T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140506T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140626T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20141123T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_20140316T2300Z.nc'),
 PosixPath('data_gpfs/realdata/MARC_F1-MARS3D-MANGAE4000_2014090

**GPFS=> tar 20.1 ms  real file 853 µs


In [24]:
%%time
mounted_dir = Path("data_lustre/mounted_dataset/data/realdata/")
list(mounted_dir.iterdir())

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 4.62 ms


[PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140101T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140102T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140103T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140104T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140105T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140106T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140107T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140108T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140109T2300Z.nc'),
 PosixPath('data_lustre/mounted_dataset/data/realdata/MARC_F1-MARS3D-MANGAE4000_20140110T23

In [25]:
%%time
mounted_dir = Path("data_lustre/realdata/")
list(mounted_dir.iterdir())

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 1.92 ms


[PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140703T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20141024T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140819T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140721T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140827T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140826T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140512T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140613T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20141017T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20141001T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140928T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1-MARS3D-MANGAE4000_20140809T2300Z.nc'),
 PosixPath('data_lustre/realdata/MARC_F1

**LUSTRE=> tar 1.18 ms  real file 925 µs

**slightly  slower to list the directory contents 

NFS got stale handle on r2i0n33, so use lustre to test xarray

## Benchmarks

In [26]:

client

<Client: 'tcp://10.148.0.160:50358' processes=168 threads=168, memory=720.72 GB>

### Original netCDF files

In [27]:
%%time
ds_orig = xr.open_mfdataset("data_lustre/realdata/*.nc", combine='nested', concat_dim='member_id')
ds_orig

CPU times: user 1min 16s, sys: 9.07 s, total: 1min 26s
Wall time: 3min 18s


<xarray.Dataset>
Dimensions:      (level: 30, member_id: 365, ni: 515, ni_f: 515, ni_u: 515, ni_v: 515, nj: 391, nj_f: 391, nj_u: 391, nj_v: 391, time: 365)
Coordinates:
    longitude_v  (nj_v, ni_v) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
    latitude_v   (nj_v, ni_v) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
    latitude_u   (nj_u, ni_u) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
    longitude    (nj, ni) float64 dask.array<chunksize=(391, 515), meta=np.ndarray>
    latitude     (nj, ni) float64 dask.array<chunksize=(391, 515), meta=np.ndarray>
    longitude_u  (nj_u, ni_u) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
  * nj           (nj) float32 0.0 1.0 2.0 3.0 4.0 ... 387.0 388.0 389.0 390.0
  * nj_f         (nj_f) float32 0.5 1.5 2.5 3.5 4.5 ... 387.5 388.5 389.5 390.5
  * level        (level) float32 -0.98333335 -0.95 ... -0.05 -0.016666668
  * ni_v         (ni_v) float32 0.0 1.0 2.0 3.0 4.0 ... 511.0 512.0 513.0 514.0
  * ni_f         (ni_f) float32 0.5 1.5 2.5 3.5 4.5 ... 511.5 512.5 513.5 514.5
  * nj_v         (nj_v) float32 0.5 1.5 2.5 3.5 4.5 ... 387.5 388.5 389.5 390.5
  * ni           (ni) float32 0.0 1.0 2.0 3.0 4.0 ... 511.0 512.0 513.0 514.0
  * ni_u         (ni_u) float32 0.5 1.5 2.5 3.5 4.5 ... 511.5 512.5 513.5 514.5
  * nj_u         (nj_u) float32 0.0 1.0 2.0 3.0 4.0 ... 387.0 388.0 389.0 390.0
  * time         (time) datetime64[ns] 2014-01-01T23:00:00 ... 2014-12-31T23:00:00
Dimensions without coordinates: member_id
Data variables:
    SIG          (member_id, level) float32 dask.array<chunksize=(1, 30), meta=np.ndarray>
    Csu_sig      (member_id, level) float32 dask.array<chunksize=(1, 30), meta=np.ndarray>
    hc           (member_id, nj, ni) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    b            (member_id) float64 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    theta        (member_id) float64 6.0 6.0 6.0 6.0 6.0 ... 6.0 6.0 6.0 6.0 6.0
    H0           (member_id, nj, ni) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    HX           (member_id, nj_u, ni_u) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    HY           (member_id, nj_v, ni_v) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    XE           (member_id, time, nj, ni) float32 dask.array<chunksize=(1, 365, 391, 515), meta=np.ndarray>
    UZ           (member_id, time, level, nj_u, ni_u) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
    VZ           (member_id, time, level, nj_v, ni_v) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
    SAL          (member_id, time, level, nj, ni) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
    TEMP         (member_id, time, level, nj, ni) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
Attributes:
    limi:                    0
    lima:                    514
    pasi:                    1
    ljmi:                    0
    ljma:                    390
    pasj:                    1
    lkmi:                    1
    lkma:                    30
    pask:                    1
    global_imin:             0
    global_imax:             514
    global_jmin:             0
    global_jmax:             390
    data_type:               OCO oriented grid
    format_version:          1.3.1
    Conventions:             CF-1.6 OCO-1.3.1 COMODO-1.0
    netcdf_version:          4.1.2
    product_version:         1.0
    references:              http://www.previmer.org/
    easting:                 longitude
    northing:                latitude
    grid_projection:         n/a
    distribution_statement:  Data restrictions: for registered users only
    institution:             IFREMER
    institution_references:  http://www.ifremer.fr/
    data_centre:             IFREMER OCO DATA CENTER
    data_centre_references:  http://www.previmer.org/
    creation_date:           2014-01-03T13:29:49Z
   

In [28]:
ds_orig.TEMP.data.visualize()

### Mounted netCDF files from the tar archive

In [29]:
%%time
ds_mntd = xr.open_mfdataset("data_lustre/mounted_dataset/data/realdata/*.nc", combine='nested', concat_dim='member_id')
ds_mntd

CPU times: user 1min 15s, sys: 4.62 s, total: 1min 20s
Wall time: 2min 28s


<xarray.Dataset>
Dimensions:      (level: 30, member_id: 365, ni: 515, ni_f: 515, ni_u: 515, ni_v: 515, nj: 391, nj_f: 391, nj_u: 391, nj_v: 391, time: 365)
Coordinates:
    longitude_v  (nj_v, ni_v) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
    latitude_v   (nj_v, ni_v) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
    latitude_u   (nj_u, ni_u) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
    longitude    (nj, ni) float64 dask.array<chunksize=(391, 515), meta=np.ndarray>
    latitude     (nj, ni) float64 dask.array<chunksize=(391, 515), meta=np.ndarray>
    longitude_u  (nj_u, ni_u) float32 dask.array<chunksize=(391, 515), meta=np.ndarray>
  * nj           (nj) float32 0.0 1.0 2.0 3.0 4.0 ... 387.0 388.0 389.0 390.0
  * nj_f         (nj_f) float32 0.5 1.5 2.5 3.5 4.5 ... 387.5 388.5 389.5 390.5
  * level        (level) float32 -0.98333335 -0.95 ... -0.05 -0.016666668
  * ni_v         (ni_v) float32 0.0 1.0 2.0 3.0 4.0 ... 511.0 512.0 513.0 514.0
  * ni_f         (ni_f) float32 0.5 1.5 2.5 3.5 4.5 ... 511.5 512.5 513.5 514.5
  * nj_v         (nj_v) float32 0.5 1.5 2.5 3.5 4.5 ... 387.5 388.5 389.5 390.5
  * ni           (ni) float32 0.0 1.0 2.0 3.0 4.0 ... 511.0 512.0 513.0 514.0
  * ni_u         (ni_u) float32 0.5 1.5 2.5 3.5 4.5 ... 511.5 512.5 513.5 514.5
  * nj_u         (nj_u) float32 0.0 1.0 2.0 3.0 4.0 ... 387.0 388.0 389.0 390.0
  * time         (time) datetime64[ns] 2014-01-01T23:00:00 ... 2014-12-31T23:00:00
Dimensions without coordinates: member_id
Data variables:
    SIG          (member_id, level) float32 dask.array<chunksize=(1, 30), meta=np.ndarray>
    Csu_sig      (member_id, level) float32 dask.array<chunksize=(1, 30), meta=np.ndarray>
    hc           (member_id, nj, ni) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    b            (member_id) float64 0.0 0.0 0.0 0.0 0.0 ... 0.0 0.0 0.0 0.0 0.0
    theta        (member_id) float64 6.0 6.0 6.0 6.0 6.0 ... 6.0 6.0 6.0 6.0 6.0
    H0           (member_id, nj, ni) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    HX           (member_id, nj_u, ni_u) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    HY           (member_id, nj_v, ni_v) float32 dask.array<chunksize=(1, 391, 515), meta=np.ndarray>
    XE           (member_id, time, nj, ni) float32 dask.array<chunksize=(1, 365, 391, 515), meta=np.ndarray>
    UZ           (member_id, time, level, nj_u, ni_u) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
    VZ           (member_id, time, level, nj_v, ni_v) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
    SAL          (member_id, time, level, nj, ni) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
    TEMP         (member_id, time, level, nj, ni) float32 dask.array<chunksize=(1, 365, 30, 391, 515), meta=np.ndarray>
Attributes:
    limi:                    0
    lima:                    514
    pasi:                    1
    ljmi:                    0
    ljma:                    390
    pasj:                    1
    lkmi:                    1
    lkma:                    30
    pask:                    1
    global_imin:             0
    global_imax:             514
    global_jmin:             0
    global_jmax:             390
    data_type:               OCO oriented grid
    format_version:          1.3.1
    Conventions:             CF-1.6 OCO-1.3.1 COMODO-1.0
    netcdf_version:          4.1.2
    product_version:         1.0
    references:              http://www.previmer.org/
    easting:                 longitude
    northing:                latitude
    grid_projection:         n/a
    distribution_statement:  Data restrictions: for registered users only
    institution:             IFREMER
    institution_references:  http://www.ifremer.fr/
    data_centre:             IFREMER OCO DATA CENTER
    data_centre_references:  http://www.previmer.org/
    creation_date:           2014-01-03T13:29:49Z
   

In [30]:
ds_mntd.TEMP.data.visualize()

### Benchmark: Yearly Averages

In [ ]:
%%time
ds_orig.groupby('time.year').mean(['time', 'member_id']).compute()

In [ ]:
%%time
ds_mntd.groupby('time.year').mean(['time', 'member_id']).compute()

### Dask Performance Reports

In [ ]:
with performance_report(filename="dask-perf-report-original.html"):
    ds_orig.groupby('time.year').mean(['time', 'member_id']).compute()

In [ ]:
with performance_report(filename="dask-perf-report-mounted.html"):
    ds_mntd.groupby('time.year').mean(['time', 'member_id']).compute()

In [ ]:
from IPython.display import HTML

In [ ]:
display(HTML("dask-perf-report-original.html"))

In [ ]:
display(HTML("dask-perf-report-mounted.html"))

### test under GPFS

In [ ]:
%%time
ds_orig_gpfs = xr.open_mfdataset("data_gpfs/realdata/*.nc", combine='nested', concat_dim='member_id')
ds_orig_gpfs

In [ ]:
%%time
ds_mntd_gpfs= xr.open_mfdataset("data_gpfs/mounted_dataset/data/realdata/*.nc", combine='nested', concat_dim='member_id')
ds_mntd_gpfs

### Benchmark: Yearly Averages GPFS


In [ ]:
%%time
ds_orig_gpfs.groupby('time.year').mean(['time', 'member_id']).compute()

In [ ]:
%%time
ds_mntd_gpfs.groupby('time.year').mean(['time', 'member_id']).compute()

### Dask Performance Reports GPFS

In [ ]:
with performance_report(filename="dask-perf-report-original-gpfs.html"):
    ds_orig_gpfs.groupby('time.year').mean(['time', 'member_id']).compute()

In [ ]:
with performance_report(filename="dask-perf-report-mounted-gpfs.html"):
    ds_mntd_gpfs.groupby('time.year').mean(['time', 'member_id']).compute()

In [ ]:
from IPython.display import HTML

In [ ]:
display(HTML("dask-perf-report-original-gpfs.html"))

In [ ]:
display(HTML("dask-perf-report-mounted-gpfs.html"))